### API's

Una API es una interfaz para comunicarnos con un software que está corriendo en algún servidor remoto. Normalmente, una API se usa para obtener datos acerca de algún tema en específico. Diferentes compañías, instituciones, universidades, etc, tienen APIs para que nosotros (programadores/desarrolladores/científicos de datos) podamos construir programas usando los datos que ofrecen. Hay una infinidad de APIs que ofrecen una gran diversidad de información.

En esta ocasión, vamos a aprender a adquirir datos de una nueva fuente: las APIs. Vamos a usar la [API de la NASA](https://api.nasa.gov/) para obtener datos acerca de los objetos que orbitan cerca de la Tierra.

A continuación vamos a aprender a comunicarnos con una para pedir datos y vamos a aprender a automatizar nuestras peticiones. Pero primero, un poquito de teoría.

#### Peticiones HTTP

Una peticiones HTTP es una solicitud de información de un cliente a un servidor usando el protocolo HTTP. El protocolo HTTP es simplemente una serie de reglas que nos dicen cuál es la manera apropiada de comunicarnos con el servidor.

#### Endpoints y URLs

Los URLs son las direcciones a donde pedimos información. Una API tiene normalmente una documentación donde te indica cuáles son los URLs disponibles. Cada URL apunta hacia información o recursos distintos. Usamos algún tipo de software ([Postman](https://www.postman.com/) o [Requests](https://requests.readthedocs.io/en/latest/user/quickstart/#make-a-request)) para "llamar" dicho endpoint (URL) y aplicar una acción.

#### Verbos HTTP

Cuando realizamos una petición HTTP usamos 1 tipo de "verbo", que indica la acción que queremos realizar. Hay muchos verbos, pero 5 son los más importantes:

- GET: Lo usamos cuando queremos **pedir información**
- POST: Lo usamos cuando queremos **enviar información** para crear algo (una cuenta de usuario, por ejemplo)
- PUT: Lo usamos cuando queremos **sustituir** algún dato por otro
- PATCH: Lo usamos cuando queremos **modificar** algún dato
- DELETE: Lo usamos cuando queremos **eliminar** algún dato

Para los propósitos de la adquisición de datos, el verbo que más nos interesa es el verbo GET (si quieres saber más sobre los demás verbos, puedes ir aquí), así que usaremos solamente ese.

#### Parámetros

Cuando hacemos una solicitud HTTP, normalmente vamos a tener que enviar parámetros para delimitar nuestras búsquedas. Los parámetros funcionan de manera similar a los parámetros de las funciones, tienen un nombre y le pasamos un valor como argumento. Los parámetros que enviemos determinarán qué datos vamos a obtener de regreso y en qué forma.

Respuestas

Las respuestas son los datos que recibimos de una API. Normalmente los datos que se transfieren a través de una API están en formato JSON. Las respuestas contienen los datos que solicitamos, algo "metadata" (datos acerca de los datos) y un estatus de la petición.

#### Estatus de la petición

Cuando recibimos una respuesta, también vamos a recibir un código de estatus que sirve para identificar cuál fue el resultado de nuestra solicitud. También hay muchísimos estatus distintos, pero los más importantes son los siguientes:

    200: Todo salió bien.
    201: Los recursos que querías crear fueron creados con éxito
    404: El recurso no fue encontrado en ese URL
    400: Los datos que enviaste son incorrectos
    500: Hubo un error interno en el servidor

#### Librería Requests

¡Estamos listos para hacer nuestras peticiones HTTP! Antes que nada, hay que instalar la librería de Python que usaremos para hacer nuestras peticiones: requests.

En una celda usa el comando !pip install requests para instalar la librería.

Ahora, necesitamos un API. Vamos a explorar un API que ofrece la NASA acerca de objetos en el espacio cuya órbita pasa cerca de la Tierra. Puedes encontrar dicha API y su documentación aquí. Para poder acceder a la API, necesitamos registrarnos en la página de la NASA y obtener lo que se llama un Api Key, que es un tipo contraseña que necesitamos para hacer peticiones a su API. Puedes obtener tu propia Api Key registrándote aquí.

Entonces, vamos a importar requests en un Jupyter Notebooks:

In [21]:
#Recuerda instalar el paquete: /usr/local/opt/python@3.10/bin/python3.10 -m pip install requests
import requests

Según la documentación, el siguiente es el url al que podemos pedir datos acerca de estos objetos que orbitan cerca de la Tierra:

In [2]:
endpoint = 'https://api.nasa.gov/neo/rest/v1/neo/browse/'

Vamos a realizar una petición GET usando requests a ver qué pasa:

In [3]:
r = requests.get(endpoint)

Ok... ¿Y ahora qué?

Un primer paso sería revisar el estatus de la llamada:

In [4]:
r.status_code

403

El estatus 403 significa que el recurso está prohibido. Podemos ver un poco más de información pidiendo el cuerpo de la respuesta en formato json:

In [5]:
r.json()

{'error': {'code': 'API_KEY_MISSING',
  'message': 'No api_key was supplied. Get one at https://api.nasa.gov:443'}}

¡Lo que pasa es que no hemos mandado la API Key!

Según la documentación, debemos generar y envíar la API Key como parámetro en la petición. La API Key se genera en la propia página y una vez generada, podemos agregarla a los parámetros de la siguiente manera:

In [6]:
payload = {'api_key': 'mgxsP3tHJSsJhz67rGcwRKlx6CY6dSJmup29nPMg'}

#probamos de nuevo la conexión con la api ('params =' puede omitirse)
r = requests.get(endpoint, params = payload)

In [7]:
r.status_code

200

Éxito!

Si revisamos los datos enviados en la respuesta podemos ver que ya tenemos algo que parece útil:

In [8]:
json = r.json()

Para entender mejor este json, vamos a revisar las keys primero:

In [9]:
json.keys()

dict_keys(['links', 'page', 'near_earth_objects'])

Ok, veamos qué hay en links:

In [10]:
json['links']

{'next': 'http://api.nasa.gov/neo/rest/v1/neo/browse?page=1&size=20&api_key=mgxsP3tHJSsJhz67rGcwRKlx6CY6dSJmup29nPMg',
 'self': 'http://api.nasa.gov/neo/rest/v1/neo/browse?page=0&size=20&api_key=mgxsP3tHJSsJhz67rGcwRKlx6CY6dSJmup29nPMg'}

Esta metadata nos dice qué link es el que solicitamos (self) y cuál es el siguiente link que tendríamos que usar para pedir los datos posteriores (next). Esto está buenísimo porque nos permite automatizar nuestras llamadas. Al saber siempre cuál es el link que sigue podemos extraerlo de ahí y realizar una nueva llamada.

Veamos qué hay en page:

In [11]:
json['page']

{'size': 20, 'total_elements': 31987, 'total_pages': 1600, 'number': 0}

Esta es información sobre la "página" que hemos pedido. Como si fuera un libro, cada página tiene una cierta cantidad de información. Podemos ver que esta página tiene 20 entradas (size), que el total de elementos que hay en la base de datos es de 23777 (total_elements), que el total de páginas es de 1189 (que como podrás imaginar, es 23777 dividido entre 20), y que la página actual es la 0 (number).

Ahora veamos near_earth_objects:

In [12]:
json['near_earth_objects']

[{'links': {'self': 'http://api.nasa.gov/neo/rest/v1/neo/2000433?api_key=mgxsP3tHJSsJhz67rGcwRKlx6CY6dSJmup29nPMg'},
  'id': '2000433',
  'neo_reference_id': '2000433',
  'name': '433 Eros (A898 PA)',
  'name_limited': 'Eros',
  'designation': '433',
  'nasa_jpl_url': 'http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2000433',
  'absolute_magnitude_h': 10.31,
  'estimated_diameter': {'kilometers': {'estimated_diameter_min': 23.0438466577,
    'estimated_diameter_max': 51.5276075896},
   'meters': {'estimated_diameter_min': 23043.8466576534,
    'estimated_diameter_max': 51527.6075895943},
   'miles': {'estimated_diameter_min': 14.3187780415,
    'estimated_diameter_max': 32.0177610556},
   'feet': {'estimated_diameter_min': 75603.1738682955,
    'estimated_diameter_max': 169053.8360842445}},
  'is_potentially_hazardous_asteroid': False,
  'close_approach_data': [{'close_approach_date': '1900-12-27',
    'close_approach_date_full': '1900-Dec-27 01:30',
    'epoch_date_close_approach': -21778794000

¡Estos son nuestros datos! Podemos ver que tenemos una lista con diccionarios dentro. Esto es algo que podemos leer directamente en pandas. Vamos a hacer eso. Debido a que el json que tenemos tiene muchos datos "anidados" (diccionarios dentro de diccionarios dentro de diccionarios), necesitamos primero "normalizar" nuestros datos. Esto básicamente significa extraer los datos anidados para convertirlos en su propia columna (puedes aprender más sobre este proceso [aquí](https://www.kaggle.com/code/jboysen/quick-tutorial-flatten-nested-json-in-pandas/notebook)). Simplemente hay que usar el siguiente código:

In [13]:
import pandas as pd

normalized = pd.json_normalize(json['near_earth_objects'])

Y ahora creamos un DataFrame usando from_dict:

In [14]:
df = pd.DataFrame.from_dict(normalized)
df.head()

id neo_reference_id                    name name_limited designation  \
0  2000433          2000433      433 Eros (A898 PA)         Eros         433   
1  2000719          2000719    719 Albert (A911 TB)       Albert         719   
2  2000887          2000887    887 Alinda (A918 AA)       Alinda         887   
3  2001036          2001036  1036 Ganymed (A924 UB)      Ganymed        1036   
4  2001221          2001221    1221 Amor (1932 EA1)         Amor        1221   

                                    nasa_jpl_url  absolute_magnitude_h  \
0  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2000433                 10.31   
1  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2000719                 15.59   
2  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2000887                 13.83   
3  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2001036                  9.21   
4  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2001221                 17.38   

   is_potentially_hazardous_asteroid  \
0                              False   
1                              False   
2                              False   
3                              False   
4                              False   

                                 close_approach_data  is_sentry_object  ...  \
0  [{'close_approach_date': '1900-12-27', 'close_...             False  ...   
1  [{'close_approach_date': '1909-08-21', 'close_...             False  ...   
2  [{'close_approach_date': '1910-01-04', 'close_...             False  ...   
3  [{'close_approach_date': '1910-02-25', 'close_...             False  ...   
4  [{'close_approach_date': '1900-03-08', 'close_...             False  ...   

  orbital_data.perihelion_distance  orbital_data.perihelion_argument  \
0                1.133284372081002                 178.9269951795186   
1                1.194521856699832                 156.2503681565663   
2                1.061321201691673                 350.4750170863266   
3                1.244963116352242                 132.4678966101859   
4                1.082508630279756                 26.63044254343605   

   orbital_data.aphelion_distance  orbital_data.perihelion_time  \
0               1.782973900121676          2459802.601698595905   
1               4.079828798274502          2459956.023234576328   
2               3.883609285637057          2460678.792844276833   
3               4.086971558467183          2460569.530751867419   
4               2.755083241500687          2459867.321948764327   

   orbital_data.mean_anomaly  orbital_data.mean_motion  orbital_data.equinox  \
0          110.7776526746434         .5597706088868498                 J2000   
1          10.23596432405304         .2301418330795496                 J2000   
2          188.0405622566953         .2535179888660634                 J2000   
3          231.1579652330964         .2264236763023365                 J2000   
4          49.38482790190183         .3708180698222572                 J2000   

   orbital_data.orbit_class.orbit_class_type  \
0                                        AMO   
1                                        AMO   
2                                        AMO   
3                                        AMO   
4                                        AMO   

    orbital_data.orbit_class.orbit_class_description  \
0  Near-Earth asteroid orbits similar to that of ...   
1  Near-Earth asteroid orbits similar to that of ...   
2  Near-Earth asteroid orbits similar to that of ...   
3  Near-Earth asteroid orbits similar to that of ...   
4  Near-Earth asteroid orbits similar to that of ...   

  orbital_data.orbit_class.orbit_class_range  
0         1.017 AU < q (perihelion) < 1.3 AU  
1         1.017 AU < q (perihelion) < 1.3 AU  
2         1.017 AU < q (perihelion) < 1.3 AU  
3         1.017 AU < q (perihelion) < 1.3 AU  
4         1.017 AU < q (perihelion) < 1.3 AU  

[5 rows x 44 columns]

¡Listo! Ya tenemos un DataFrame con nuestros datos.

Ahora, estas son sólo 20 entradas de un total de 23777. Si queremos hacer un verdadero análisis, vamos a necesitar un poco más de datos. Hacer estas peticiones manualmente nos tomaría años, así que vamos a utilizar algunas herramientas de Python para automatizar este proceso.

#### For Loops

Los for loops son operadores de control de flujo que sirven para realiza iteraciones, lo cual puede ser utilizado para ejecutar un mismo código repetidas veces. Un for loop se ve así:

In [15]:
#No se incluye el último número del rango
for i in range(1, 10):
    print(i)

1
2
3
4
5
6
7
8
9


Vamos a diseccionarlo.

range(0, 10) le indica a Python que queremos iterar en el rango de 0 a 9 (el último número nunca se incluye).

for i in significa que "cada iteración que realicemos, el valor que le corresponda a dicha iteración va a ser asignado a una variable llamada i".

Después escribimos dos puntos (:) y el bloque del for loop. En este caso, en el bloque estamos imprimiendo el valor de i que es el valor obtenido de range(0, 10) en cada iteración.

Vamos a usar un for loop para realizar 10 peticiones a la API de la NASA de manera automática.

En cada iteración hacemos la llamada, revisamos el estatus, extraemos los datos correspondientes y después usamos [links][next] para obtener el nuevo link y repetir la operación. Como el valor del for loop no va a ser utilizado (sólo queremos repetir el código 10 veces y ya), podemos escribir _ en vez de i:

In [16]:
#Incompleto NO CORRER
for _ in range(0, 10):
    r = requests.get(endpoint, params = payload)

    if r.status_code == 200:
        json = r.json()

        data = json['near_earth_objects']
        new_link = json['links']['next']

        endpoint = new_link

Fíjate en la última línea donde asignamos endpoint = new_link para que en la siguiente iteración la petición se haga al nuevo link.

Es una buena práctica esperar un poco entre cada petición. Para eso vamos a usar la librería time para esperar 5 segundos entre cada petición:

In [17]:
#Icompleto NO CORRER
import time

for _ in range(0, 10):
    r = requests.get(endpoint, params = payload)

    if r.status_code == 200:
        json = r.json()

        data = json['near_earth_objects']
        new_link = json['links']['next']

        endpoint = new_link

    time.sleep(5)

Ahora, ¿qué hacemos con nuestros datos? ¿cómo los podemos guardar para utilizarlos después? Podríamos tener un diccionario donde guardemos los nuevos datos en cada iteración. La llave va a ser el número de iteración. Para lograr esto necesitamos volver a definir i y agregar los datos a un diccionario llamado dict_datos:

In [18]:
#Completo, es posible correr aunque tarda un poco (son 10 peticiones al servicio)
import time

dict_datos = {}

for i in range(0, 10):
    r = requests.get(endpoint, params = payload)

    if r.status_code == 200:
        json = r.json()

        data = json['near_earth_objects']
        dict_datos[i] = data
        
        new_link = json['links']['next']
        endpoint = new_link

    time.sleep(5)

Veamos qué hay en dict_datos:

In [19]:
dict_datos

{0: [{'links': {'self': 'http://api.nasa.gov/neo/rest/v1/neo/2099799?api_key=mgxsP3tHJSsJhz67rGcwRKlx6CY6dSJmup29nPMg'},
   'id': '2099799',
   'neo_reference_id': '2099799',
   'name': '99799 (2002 LJ3)',
   'designation': '99799',
   'nasa_jpl_url': 'http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2099799',
   'absolute_magnitude_h': 18.45,
   'estimated_diameter': {'kilometers': {'estimated_diameter_min': 0.5426939457,
     'estimated_diameter_max': 1.2135005535},
    'meters': {'estimated_diameter_min': 542.6939456932,
     'estimated_diameter_max': 1213.5005535475},
    'miles': {'estimated_diameter_min': 0.3372142797,
     'estimated_diameter_max': 0.7540340525},
    'feet': {'estimated_diameter_min': 1780.492004788,
     'estimated_diameter_max': 3981.3011561007}},
   'is_potentially_hazardous_asteroid': False,
   'close_approach_data': [{'close_approach_date': '1912-08-21',
     'close_approach_date_full': '1912-Aug-21 09:07',
     'epoch_date_close_approach': -1810219980000,
     'relat

¿Ves? Tenemos un diccionario donde cada llave contiene una de las listas de jsons que obtenemos en cada llamada.

Ahora, vamos a poner un método de seguridad para asegurarnos que nuestra automatización no vaya a fallar.

#### Excepciones

Hay veces que algún error (una Exception) sucede durante la ejecución de nuestro programa, Python lo detecta y detiene el programa completo para evitar que el error cause problemas. Por ejemplo, aquí tenemos un error que sucede durante la lectura de una llave inexistente en un diccionario:


In [20]:
dict = {
    0: ['a', 'b', 'c'],
    1: ['d', 'e', 'f'],
    2: ['g', 'h', 'i']
}

dict[3]

KeyError: 3

Este error podría suceder durante la lectura de la respuesta a nuestra petición, cuando accedemos a near_earth_object o a links. Si este error sucediera, nuestro programa se detendría. Dado que lo que queremos es automatizar este proceso, dejar que nuestro programa se detenga suena a una muy mala idea.

Para evitar que eso suceda, usamos una estructura llamada **try - except**. Básicamente lo que sucede es que cierto código se intenta correr durante el bloque de try, y si ese código lanza una excepción (un error), en vez de detener el programa el bloque de except se corre para que tú puedas hacer algo para lidiar con el problema. En nuestro ejemplo, esto se vería así:

In [22]:
try:
    dict[3]
except:
    print('La llave no existe en nuestro diccionario')

La llave no existe en nuestro diccionario


Vamos a agregar un try except a nuestro for loop para evitar que haya errores que arruinen nuestro programa. También voy a agregar un parámetro timeout=5 a mi petición GET. Esto significa que cada vez que hagamos una llamada, vamos a esperar durante 5 segundos a obtener una respuesta. Si no obtenemos respuesta, se lanza un error. Esto sirve para evitar que nuestro programa se quede esperando durante años para obtener una respuesta. Dado que la agregación del timeout significa que puede haber un error de timeout, vamos a envolver todo el código del bloque for loop con nuestro try except. De esta manera "cachamos" cualquier error que suceda ahí:

In [23]:
dict_datos = {}

for i in range(0, 10):
    try:
        time.sleep(5)
        r = requests.get(endpoint, params = payload, timeout = 5)

        if r.status_code == 200:
            json = r.json()

            data = json['near_earth_objects']
            dict_datos[i] = data
            
            new_link = json['links']['next']
            endpoint = new_link

    except:
        continue

En el bloque de except lo único que estoy haciendo es agregar un continue. Esto le indica a Python "si hay un error, simplemente continúa con la siguiente iteración". Obviamente la petición se va a realizar a la misma URL de la iteración que falló. Podríamos agregar lógica para intentar evitar esto, pero eso se quedará pendiente para alguna otra ocasión.

Observa también que cambié el lugar de time.sleep(5), para asegurarme de que se corra ese código en cada iteración, sin importar si hay un error o no.

Ahora que ya tenemos nuestro programa para obtener nuestros datos, necesitamos saber qué hacer con esos datos. Sobre todo, es necesario aprender a juntar todos nuestros datos obtenidos en un mismo DataFrame. Para eso vamos a aprender a concatenar DatFrames.

#### Concatenación de DataFrames

Otra de las principales tareas de un Data Wrangler es la de unir conjuntos de datos en un solo DataFrame. Dado que los datos que hemos estado obteniendo están separados en pedazos (chunks, como les dicen en su casa), vamos a aprender una de las técnicas que existen para unir DataFrames, la concatenación. En realidad, en esta instancia en particular, una opción más directa hubiera sido simplemente unir la lista que obtenemos en cada iteración con una lista principal que contenga todas las entradas. Pero vamos a aprovechar la fragmentación de nuestro dataset para aprender sobre concatenación.

Primero que nada, voy a usar otro for loop para iterar por todas las llaves de nuestro diccionario. Si uso la misma estructura, pero en lugar de range(0, 10) itero sobre el diccionario, cada i se convierte en una de las llaves de nuestro diccionario:


In [24]:
for par in dict_datos:
    print(par)

0
1
2
3
4
5
6
7
8
9


Entonces, en cada iteración voy a normalizar la lista de diccionarios, voy a convertirla en un DataFrame y la voy a guardar en el mismo diccionario, reemplazando el valor anterior por uno nuevo:

In [25]:
for par in dict_datos:
    normalized = pd.json_normalize(dict_datos[par])
    df = pd.DataFrame.from_dict(normalized)
    dict_datos[par] = df

Ahora todos nuestros valores son DataFrames:

In [26]:
primer_df = dict_datos[0]
primer_df.head()

id neo_reference_id                name designation  \
0  2153951          2153951   153951 (2002 AC3)      153951   
1  2153953          2153953   153953 (2002 AD9)      153953   
2  2153957          2153957  153957 (2002 AB29)      153957   
3  2153958          2153958  153958 (2002 AM31)      153958   
4  2154007          2154007    154007 (2002 BY)      154007   

                                    nasa_jpl_url  absolute_magnitude_h  \
0  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153951                 18.74   
1  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153953                 16.84   
2  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153957                 17.76   
3  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153958                 18.37   
4  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2154007                 18.13   

   is_potentially_hazardous_asteroid  \
0                              False   
1                              False   
2                              False   
3                               True   
4                              False   

                                 close_approach_data  is_sentry_object  \
0  [{'close_approach_date': '1900-01-27', 'close_...             False   
1  [{'close_approach_date': '1912-03-02', 'close_...             False   
2  [{'close_approach_date': '1937-09-20', 'close_...             False   
3  [{'close_approach_date': '1903-07-19', 'close_...             False   
4  [{'close_approach_date': '1904-04-06', 'close_...             False   

                                          links.self  ...  \
0  http://api.nasa.gov/neo/rest/v1/neo/2153951?ap...  ...   
1  http://api.nasa.gov/neo/rest/v1/neo/2153953?ap...  ...   
2  http://api.nasa.gov/neo/rest/v1/neo/2153957?ap...  ...   
3  http://api.nasa.gov/neo/rest/v1/neo/2153958?ap...  ...   
4  http://api.nasa.gov/neo/rest/v1/neo/2154007?ap...  ...   

   orbital_data.perihelion_distance  orbital_data.perihelion_argument  \
0                 1.207145723284368                 215.0703586037131   
1                 .3385615822360984                 9.787573943053527   
2                  .611043180350559                 73.18971558680613   
3                 .9342201867475185                 197.9607541044618   
4                 1.188103652538204                 23.76738574904365   

   orbital_data.aphelion_distance  orbital_data.perihelion_time  \
0                2.46475024644563          2459640.412008480873   
1               3.207733277288319          2459971.155090096723   
2               4.453791380910145          2459696.959212552623   
3               2.472129658616169          2460224.187823076566   
4               2.448975468530991          2459632.769512668028   

   orbital_data.mean_anomaly  orbital_data.mean_motion  orbital_data.equinox  \
0          142.6665480099816         .3961991273524697                 J2000   
1          12.24953446768571         .4174330235826562                 J2000   
2          74.23662642177354         .2445688668269778                 J2000   
3          260.8123648364727         .4434199135174934                 J2000   
4          147.7915423609133         .4019017934389893                 J2000   

   orbital_data.orbit_class.orbit_class_type  \
0                                        AMO   
1                                        APO   
2                                        APO   
3                                        APO   
4                                        AMO   

    orbital_data.orbit_class.orbit_class_description  \
0  Near-Earth asteroid orbits similar to that of ...   
1  Near-Earth asteroid orbits which cross the Ear...   
2  Near-Earth asteroid orbits which cross the Ear...   
3  Near-Earth asteroid orbits which cross the Ear...   
4  Near-Earth asteroid orbits similar to that of ...   

          orbital_data.orbit_class.orbit_class_range  
0                 1.017 AU < q (perihelion) < 1.3 AU  
1  a (semi-major axis) > 1.0 AU; q (perihelion) <...  
2  a (semi-major 

Vamos a juntarlos todos en un gran, rechoncho y sanote DataFrame. Pero primero, vamos a entender bien cómo funciona pd.concat.

pandas ofrece varias maneras de unir DataFrames un solo DataFrame. Una de ellas es la función pd.concat. pd.concat te permite concatenar Series y DataFrames usando diferentes axis. Comencemos con las Series.

##### pd.concat con Series

Tenemos las siguientes dos Series:


In [27]:
serie_1 = pd.Series([1, 2, 3], index = ['a', 'b', 'c'])
serie_2 = pd.Series([4, 5, 6,], index = ['d', 'e', 'f'])

In [28]:
serie_1

a    1
b    2
c    3
dtype: int64

In [29]:
serie_2

d    4
e    5
f    6
dtype: int64

Podemos unirlas de manera vertical llamando pd.concat con axis=0. Observa que tenemos que pasarle las dos Series dentro de una lista:

In [30]:
pd.concat([serie_1, serie_2], axis = 0)

a    1
b    2
c    3
d    4
e    5
f    6
dtype: int64

Si queremos unirlas horizontalmente, podemos llamar la función usando axis = 1:

In [31]:
pd.concat([serie_1, serie_2], keys = ['serie_1', 'serie_2'], axis = 1)

serie_1  serie_2
a      1.0      NaN
b      2.0      NaN
c      3.0      NaN
d      NaN      4.0
e      NaN      5.0
f      NaN      6.0

Aquí hay dos cosas que observar:

- Usé el argumento keys para ponerle nombre a las columnas (ya que las Series originales no tenían nombres).

- Debido a que las Series tienen diferentes índices, la concatenación horizontal deja muchos valores vacíos. Esto se debe a que la serie_1 no tiene valores que correspondan a los índices 'd', 'f', y 'e'; mientras que la serie_2 no tiene valores que correspondan a los índices 'a', 'b', y 'c'.

Mira lo que pasa si concatenamos dos Series que compartan el mismo índice:

In [32]:
serie_3 = pd.Series([7, 8, 9], index = ['a', 'b', 'c'])

pd.concat([serie_1, serie_3], keys = ['serie_1', 'serie_3'], axis = 1)

serie_1  serie_3
a        1        7
b        2        8
c        3        9

Como ves, el índice se repite. Hay veces que esto es justo lo que queremos, pero en este caso, no parece muy deseable. En este caso tenemos dos opciones.

- Si no nos interesa mucho el índice actual, podemos resetearlo para obtener uno nuevo donde no haya repeticiones:

In [33]:
pd.concat([serie_1, serie_3], axis = 0)

a    1
b    2
c    3
a    7
b    8
c    9
dtype: int64

In [34]:
pd.concat([serie_1, serie_3], axis = 0).reset_index(drop = True)

0    1
1    2
2    3
3    7
4    8
5    9
dtype: int64

- En caso de que sí nos interese el índice, pero queramos poder diferenciar entre los índices que vienen de la serie_1 y los que vienen de la serie_3, podemos usar el argumento keys para agregar un segundo nivel en el índice:

In [35]:
pd.concat([serie_1, serie_3], keys = ['serie_1', 'serie_3'], axis = 0)

serie_1  a    1
         b    2
         c    3
serie_3  a    7
         b    8
         c    9
dtype: int64

In [36]:
concat_1 = pd.concat([serie_1, serie_3], keys = ['serie_1', 'serie_3'], axis = 0)

¿Y eso qué es? ¿Un segundo nivel de índice? Pues sí, aunque no lo creas, podemos crear diferentes niveles de índices que nos ayudan a segmentar nuestros datos a más detalle. Existen los Multiíndices de filas y también de columnas. En este caso, tenemos uno de filas.

##### Pequeña digresión para hablar sobre Multíndices en Filas

Que no cunda el pánico. Si quisieras acceder a tus datos usando loc simplemente tendrías que hacer algo como esto:

In [37]:
#Accediendo al valor
concat_1.loc[('serie_1', 'b')]

2

¿Ves? como primer argumento a nuestro loc, en vez de un solo valor, le pasamos una tupla de valores. Una tupla es eso que ves dentro de dos paréntesis (('serie_1', 'b')). Es una manera de contener dos o más valores. En este caso, nuestros dos valores son los dos niveles de nuestro índice que queremos acceder: primero serie_1 y después b. Si queremos acceder al índice b de la serie_3, haríamos lo siguiente:

In [38]:
concat_1.loc[('serie_3', 'b')]

8

Podríamos concatenar muchas Series con los mismos índices y mantenerlas segmentadas usando multi índices:

In [39]:
serie_4 = pd.Series([10, 11, 12], index = ['a', 'b', 'c'])
serie_5 = pd.Series([13, 14, 15], index = ['a', 'b', 'c'])

concat_2 = pd.concat([serie_1, serie_3, serie_4, serie_5], axis = 0, keys = ['serie_1', 'serie_3', 'serie_4', 'serie_5'])

concat_2

serie_1  a     1
         b     2
         c     3
serie_3  a     7
         b     8
         c     9
serie_4  a    10
         b    11
         c    12
serie_5  a    13
         b    14
         c    15
dtype: int64

Lo más genial es que si accedemos a la nueva Serie usando sólo el primer nivel, obtenemos una de nuestras Series completa:

In [40]:
concat_2.loc['serie_4']

a    10
b    11
c    12
dtype: int64

Pero bueno, salgamos de nuestra pequeña digresión para hablar sobre la concatenación de DataFrames.

pd.concat con DataFrames

La misma lógica aplica para la unión de DataFrames. Tenemos ahora dos DataFrames:

In [41]:
data_1 = {
    'column_1': [1, 2, 3],
    'column_2': [4, 5, 6]
}

df_1 = pd.DataFrame(data_1, index = ['a', 'b', 'c'])

df_1

column_1  column_2
a         1         4
b         2         5
c         3         6

In [42]:
data_1 = {
    'column_1': [7, 8, 9],
    'column_2': [10, 11, 12]
}

df_2 = pd.DataFrame(data_1, index = ['d', 'e', 'f'])

df_2

column_1  column_2
d         7        10
e         8        11
f         9        12

Usamos axis=0 para concatenarlos verticalmente:

In [43]:
pd.concat([df_1, df_2], axis = 0)

column_1  column_2
a         1         4
b         2         5
c         3         6
d         7        10
e         8        11
f         9        12

Si usamos axis=1 de nuevo vamos a tener valores NaN porque los DataFrames no comparten índice:

In [44]:
pd.concat([df_1, df_2], axis = 1)

column_1  column_2  column_1  column_2
a       1.0       4.0       NaN       NaN
b       2.0       5.0       NaN       NaN
c       3.0       6.0       NaN       NaN
d       NaN       NaN       7.0      10.0
e       NaN       NaN       8.0      11.0
f       NaN       NaN       9.0      12.0

Si tenemos dos DataFrames que comparten índice, pasa lo siguiente:

In [45]:
data_1 = {
    'column_3': [7, 8, 9],
    'column_4': [10, 11, 12]
}

df_3 = pd.DataFrame(data_1, index = ['a', 'b', 'c'])

df_3

column_3  column_4
a         7        10
b         8        11
c         9        12

In [46]:
pd.concat([df_1, df_3], axis = 1)

column_1  column_2  column_3  column_4
a         1         4         7        10
b         2         5         8        11
c         3         6         9        12

Si los DataFrames comparten índice y queremos concatenarlos verticalmente, también podemos usar un multiíndice en las filas para diferenciarlos:

In [47]:
data_1 = {
    'column_1': [7, 8, 9],
    'column_2': [13, 14, 15]
}

df_4 = pd.DataFrame(data_1, index = ['a', 'b', 'c'])

df_4

column_1  column_2
a         7        13
b         8        14
c         9        15

In [48]:
df_concat = pd.concat([df_1, df_4], axis = 0, keys = ['df_1', 'df_4'])

Al igual que con las Series podemos acceder a ese DataFrame usando un solo nivel o ambos niveles:

In [49]:
df_concat

column_1  column_2
df_1 a         1         4
     b         2         5
     c         3         6
df_4 a         7        13
     b         8        14
     c         9        15

In [50]:
#Accediendo a uno de los dataframes internos
df_concat.loc['df_1']

column_1  column_2
a         1         4
b         2         5
c         3         6

In [56]:
#Accediendo a una de las columnas de un dataframe interno
df_concat.loc[('df_4', 'b')]

column_1     8
column_2    14
Name: (df_4, b), dtype: int64

In [54]:
#Accediendo a un valor en particular de un dataframe interno (el segundo parámetro del primer corchete puede ser la fila o la columna)
df_concat.loc[('df_4', 'b')]['column_2']

14

Observa bien que en la primera indexación lo que obtuvimos es un DataFrame, pero en la segunda indexación ¡obtuvimos una Serie! Esto tiene mucho sentido, ya que en el índice ('df_4', 'b') en realidad hay dos valores, el que le corresponde a la column_1 y el que le corresponde a la column_2. Finalmente para acceder a un valor en particular lo que hicimos en la tercera indexación, fue utilizar un segundo corchete y especificar la columna a la que queremos referirnos. Nota que en el primer corchete como segúndo parámetro está la fila, aquí podríamos especificar la columna en su lugar, y en el tercer corchete en lugar de especificar la columna, lo que pondríamos sería la fila de referencia. Ya habrá tiempo de practicar, no te preocupes.

##### Uniendo nuestro dataset usando pd.concat

Regresemos al fin a nuestro dataset original, el que obtuvimos de la API. Vamos a usar nuestras nuevas habilidades para unir los DataFrames en uno solo. También vamos a resetear el índice porque no nos interesa mantenerlo. Aquí está una posible solución:

In [63]:
dict_datos[0].head()

id neo_reference_id                name designation  \
0  2153951          2153951   153951 (2002 AC3)      153951   
1  2153953          2153953   153953 (2002 AD9)      153953   
2  2153957          2153957  153957 (2002 AB29)      153957   
3  2153958          2153958  153958 (2002 AM31)      153958   
4  2154007          2154007    154007 (2002 BY)      154007   

                                    nasa_jpl_url  absolute_magnitude_h  \
0  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153951                 18.74   
1  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153953                 16.84   
2  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153957                 17.76   
3  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153958                 18.37   
4  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2154007                 18.13   

   is_potentially_hazardous_asteroid  \
0                              False   
1                              False   
2                              False   
3                               True   
4                              False   

                                 close_approach_data  is_sentry_object  \
0  [{'close_approach_date': '1900-01-27', 'close_...             False   
1  [{'close_approach_date': '1912-03-02', 'close_...             False   
2  [{'close_approach_date': '1937-09-20', 'close_...             False   
3  [{'close_approach_date': '1903-07-19', 'close_...             False   
4  [{'close_approach_date': '1904-04-06', 'close_...             False   

                                          links.self  ...  \
0  http://api.nasa.gov/neo/rest/v1/neo/2153951?ap...  ...   
1  http://api.nasa.gov/neo/rest/v1/neo/2153953?ap...  ...   
2  http://api.nasa.gov/neo/rest/v1/neo/2153957?ap...  ...   
3  http://api.nasa.gov/neo/rest/v1/neo/2153958?ap...  ...   
4  http://api.nasa.gov/neo/rest/v1/neo/2154007?ap...  ...   

   orbital_data.perihelion_distance  orbital_data.perihelion_argument  \
0                 1.207145723284368                 215.0703586037131   
1                 .3385615822360984                 9.787573943053527   
2                  .611043180350559                 73.18971558680613   
3                 .9342201867475185                 197.9607541044618   
4                 1.188103652538204                 23.76738574904365   

   orbital_data.aphelion_distance  orbital_data.perihelion_time  \
0                2.46475024644563          2459640.412008480873   
1               3.207733277288319          2459971.155090096723   
2               4.453791380910145          2459696.959212552623   
3               2.472129658616169          2460224.187823076566   
4               2.448975468530991          2459632.769512668028   

   orbital_data.mean_anomaly  orbital_data.mean_motion  orbital_data.equinox  \
0          142.6665480099816         .3961991273524697                 J2000   
1          12.24953446768571         .4174330235826562                 J2000   
2          74.23662642177354         .2445688668269778                 J2000   
3          260.8123648364727         .4434199135174934                 J2000   
4          147.7915423609133         .4019017934389893                 J2000   

   orbital_data.orbit_class.orbit_class_type  \
0                                        AMO   
1                                        APO   
2                                        APO   
3                                        APO   
4                                        AMO   

    orbital_data.orbit_class.orbit_class_description  \
0  Near-Earth asteroid orbits similar to that of ...   
1  Near-Earth asteroid orbits which cross the Ear...   
2  Near-Earth asteroid orbits which cross the Ear...   
3  Near-Earth asteroid orbits which cross the Ear...   
4  Near-Earth asteroid orbits similar to that of ...   

          orbital_data.orbit_class.orbit_class_range  
0                 1.017 AU < q (perihelion) < 1.3 AU  
1  a (semi-major axis) > 1.0 AU; q (perihelion) <...  
2  a (semi-major 

In [60]:
df_comp = pd.concat([dict_datos[0], dict_datos[1], dict_datos[2], dict_datos[3], dict_datos[4], dict_datos[5], dict_datos[6], dict_datos[7], dict_datos[8], dict_datos[9]])

df_comp.tail()

id neo_reference_id                name designation  \
15  2168378          2168378  168378 (1997 ET30)      168378   
16  2168791          2168791  168791 (2000 SQ43)      168791   
17  2169352          2169352  169352 (2001 UY16)      169352   
18  2169675          2169675  169675 (2002 JM97)      169675   
19  2170013          2170013   170013 (2002 UO3)      170013   

                                     nasa_jpl_url  absolute_magnitude_h  \
15  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2168378                 16.93   
16  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2168791                 18.87   
17  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2169352                 19.36   
18  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2169675                 16.61   
19  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2170013                 17.77   

    is_potentially_hazardous_asteroid  \
15                              False   
16                              False   
17                              False   
18                              False   
19                              False   

                                  close_approach_data  is_sentry_object  \
15  [{'close_approach_date': '1913-06-27', 'close_...             False   
16  [{'close_approach_date': '1906-09-05', 'close_...             False   
17  [{'close_approach_date': '1932-11-12', 'close_...             False   
18  [{'close_approach_date': '1903-07-04', 'close_...             False   
19  [{'close_approach_date': '1903-07-21', 'close_...             False   

                                           links.self  ...  \
15  http://api.nasa.gov/neo/rest/v1/neo/2168378?ap...  ...   
16  http://api.nasa.gov/neo/rest/v1/neo/2168791?ap...  ...   
17  http://api.nasa.gov/neo/rest/v1/neo/2169352?ap...  ...   
18  http://api.nasa.gov/neo/rest/v1/neo/2169675?ap...  ...   
19  http://api.nasa.gov/neo/rest/v1/neo/2170013?ap...  ...   

    orbital_data.perihelion_argument  orbital_data.aphelion_distance  \
15                 263.4069265779657                3.09687990052385   
16                 144.7538884297181               3.453829169648748   
17                 48.38636861124175               3.164738490804329   
18                 236.4964767859835               4.211914708899647   
19                 330.1645973249501               5.306260601298779   

    orbital_data.perihelion_time  orbital_data.mean_anomaly  \
15          2459883.076501924533          37.01480234674393   
16          2460627.524116750606          182.2502355953875   
17          2459943.450871131218          18.70368102372662   
18          2460695.778355123987          207.3334027722708   
19          2460138.720415464232          333.0910498704109   

    orbital_data.mean_motion  orbital_data.equinox  \
15         .3152248310892144                 J2000   
16         .2834815434624042                 J2000   
17         .3278521757404349                 J2000   
18         .2195762259857846                 J2000   
19           .19468144441045                 J2000   

    orbital_data.orbit_class.orbit_class_type  \
15                                        AMO   
16                                        AMO   
17                                        APO   
18                                        AMO   
19                                        APO   

     orbital_data.orbit_class.orbit_class_description  \
15  Near-Earth asteroid orbits similar to that of ...   
16  Near-Earth asteroid orbits similar to that of ...   
17  Near-Earth asteroid orbits which cross the Ear...   
18  Near-Earth asteroid orbits similar to that of ...   
19  Near-Earth asteroid orbits which cross the Ear...   

           orbital_data.orbit_class.orbit_class_range name_limited  
15                 1.017 AU < q (perihelion) < 1.3 AU          NaN  
16                 1.017 AU < q (perihelion) < 1.3 AU          NaN  
17  a (semi-major axis) > 1.0 AU; q (perihelion) <...          NaN  
18                 1.017 AU < q (perihelion) < 1.3 

In [64]:
df_comp_reindexed = df_comp.reset_index(drop = True)

df_comp_reindexed.head()

id neo_reference_id                name designation  \
0  2153951          2153951   153951 (2002 AC3)      153951   
1  2153953          2153953   153953 (2002 AD9)      153953   
2  2153957          2153957  153957 (2002 AB29)      153957   
3  2153958          2153958  153958 (2002 AM31)      153958   
4  2154007          2154007    154007 (2002 BY)      154007   

                                    nasa_jpl_url  absolute_magnitude_h  \
0  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153951                 18.74   
1  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153953                 16.84   
2  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153957                 17.76   
3  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2153958                 18.37   
4  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2154007                 18.13   

   is_potentially_hazardous_asteroid  \
0                              False   
1                              False   
2                              False   
3                               True   
4                              False   

                                 close_approach_data  is_sentry_object  \
0  [{'close_approach_date': '1900-01-27', 'close_...             False   
1  [{'close_approach_date': '1912-03-02', 'close_...             False   
2  [{'close_approach_date': '1937-09-20', 'close_...             False   
3  [{'close_approach_date': '1903-07-19', 'close_...             False   
4  [{'close_approach_date': '1904-04-06', 'close_...             False   

                                          links.self  ...  \
0  http://api.nasa.gov/neo/rest/v1/neo/2153951?ap...  ...   
1  http://api.nasa.gov/neo/rest/v1/neo/2153953?ap...  ...   
2  http://api.nasa.gov/neo/rest/v1/neo/2153957?ap...  ...   
3  http://api.nasa.gov/neo/rest/v1/neo/2153958?ap...  ...   
4  http://api.nasa.gov/neo/rest/v1/neo/2154007?ap...  ...   

   orbital_data.perihelion_argument  orbital_data.aphelion_distance  \
0                 215.0703586037131                2.46475024644563   
1                 9.787573943053527               3.207733277288319   
2                 73.18971558680613               4.453791380910145   
3                 197.9607541044618               2.472129658616169   
4                 23.76738574904365               2.448975468530991   

   orbital_data.perihelion_time  orbital_data.mean_anomaly  \
0          2459640.412008480873          142.6665480099816   
1          2459971.155090096723          12.24953446768571   
2          2459696.959212552623          74.23662642177354   
3          2460224.187823076566          260.8123648364727   
4          2459632.769512668028          147.7915423609133   

   orbital_data.mean_motion  orbital_data.equinox  \
0         .3961991273524697                 J2000   
1         .4174330235826562                 J2000   
2         .2445688668269778                 J2000   
3         .4434199135174934                 J2000   
4         .4019017934389893                 J2000   

   orbital_data.orbit_class.orbit_class_type  \
0                                        AMO   
1                                        APO   
2                                        APO   
3                                        APO   
4                                        AMO   

    orbital_data.orbit_class.orbit_class_description  \
0  Near-Earth asteroid orbits similar to that of ...   
1  Near-Earth asteroid orbits which cross the Ear...   
2  Near-Earth asteroid orbits which cross the Ear...   
3  Near-Earth asteroid orbits which cross the Ear...   
4  Near-Earth asteroid orbits similar to that of ...   

          orbital_data.orbit_class.orbit_class_range name_limited  
0                 1.017 AU < q (perihelion) < 1.3 AU          NaN  
1  a (semi-major axis) > 1.0 AU; q (perihelion) <...          NaN  
2  a (semi-major axis) > 1.0 AU; q (perihelion) <...          NaN  
3  a (semi-major axis) > 1.0 AU; q (perihelion) <...          NaN  
4                 1.017 AU < q (perihelion) < 

In [65]:
df_comp_reindexed.tail()

id neo_reference_id                name designation  \
195  2168378          2168378  168378 (1997 ET30)      168378   
196  2168791          2168791  168791 (2000 SQ43)      168791   
197  2169352          2169352  169352 (2001 UY16)      169352   
198  2169675          2169675  169675 (2002 JM97)      169675   
199  2170013          2170013   170013 (2002 UO3)      170013   

                                      nasa_jpl_url  absolute_magnitude_h  \
195  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2168378                 16.93   
196  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2168791                 18.87   
197  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2169352                 19.36   
198  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2169675                 16.61   
199  http://ssd.jpl.nasa.gov/sbdb.cgi?sstr=2170013                 17.77   

     is_potentially_hazardous_asteroid  \
195                              False   
196                              False   
197                              False   
198                              False   
199                              False   

                                   close_approach_data  is_sentry_object  \
195  [{'close_approach_date': '1913-06-27', 'close_...             False   
196  [{'close_approach_date': '1906-09-05', 'close_...             False   
197  [{'close_approach_date': '1932-11-12', 'close_...             False   
198  [{'close_approach_date': '1903-07-04', 'close_...             False   
199  [{'close_approach_date': '1903-07-21', 'close_...             False   

                                            links.self  ...  \
195  http://api.nasa.gov/neo/rest/v1/neo/2168378?ap...  ...   
196  http://api.nasa.gov/neo/rest/v1/neo/2168791?ap...  ...   
197  http://api.nasa.gov/neo/rest/v1/neo/2169352?ap...  ...   
198  http://api.nasa.gov/neo/rest/v1/neo/2169675?ap...  ...   
199  http://api.nasa.gov/neo/rest/v1/neo/2170013?ap...  ...   

     orbital_data.perihelion_argument  orbital_data.aphelion_distance  \
195                 263.4069265779657                3.09687990052385   
196                 144.7538884297181               3.453829169648748   
197                 48.38636861124175               3.164738490804329   
198                 236.4964767859835               4.211914708899647   
199                 330.1645973249501               5.306260601298779   

     orbital_data.perihelion_time  orbital_data.mean_anomaly  \
195          2459883.076501924533          37.01480234674393   
196          2460627.524116750606          182.2502355953875   
197          2459943.450871131218          18.70368102372662   
198          2460695.778355123987          207.3334027722708   
199          2460138.720415464232          333.0910498704109   

     orbital_data.mean_motion  orbital_data.equinox  \
195         .3152248310892144                 J2000   
196         .2834815434624042                 J2000   
197         .3278521757404349                 J2000   
198         .2195762259857846                 J2000   
199           .19468144441045                 J2000   

     orbital_data.orbit_class.orbit_class_type  \
195                                        AMO   
196                                        AMO   
197                                        APO   
198                                        AMO   
199                                        APO   

      orbital_data.orbit_class.orbit_class_description  \
195  Near-Earth asteroid orbits similar to that of ...   
196  Near-Earth asteroid orbits similar to that of ...   
197  Near-Earth asteroid orbits which cross the Ear...   
198  Near-Earth asteroid orbits similar to that of ...   
199  Near-Earth asteroid orbits which cross the Ear...   

            orbital_data.orbit_class.orbit_class_range name_limited  
195                 1.017 AU < q (perihelion) < 1.3 AU          NaN  
196                 1.017 AU < q (perihelion) < 1.3 AU          NaN  
197  a (semi-major axis) > 1.0 AU; q (perihelion) <...    

Ya que tenemos las primeras 10 páginas de la API guardadas en un DataFrame, no queremos tener que volver a repetir todo el proceso. Para evitar esto, podemos guardar nuestro DataFrame en un archivo .csv para acceder a él después:

In [66]:
#guardando un dataframe en un archivo .csv
df_comp_reindexed.to_csv('../Datasets/near_earth_objects-raw.csv')